In [1]:
from das.distributed_atom_space import DistributedAtomSpace, QueryOutputFormat
from das.database.db_interface import UNORDERED_LINK_TYPES
from das.pattern_matcher.pattern_matcher import PatternMatchingAnswer, OrderedAssignment, UnorderedAssignment, CompositeAssignment, Node, Link, Variable, Not, And, Or, TypedVariable, LinkTemplate
from das.database.db_interface import WILDCARD
from das.expression_hasher import ExpressionHasher
import warnings
import numpy as np
from itertools import combinations
warnings.filterwarnings('ignore')
TARGET_NODES = None
das = DistributedAtomSpace()
db = das.db
db.prefetch()
das.count_atoms()

Log initialized. Log file: /tmp/das.log


(25, 60)

In [2]:
USE_SUBSTRING = False

if USE_SUBSTRING:
    TARGET_TYPE = "Concept"
    TARGET_SUBSTRING = "gl"
else:
    TARGET_NODES = [
        Node("Concept", "ugly")
    ]

NGRAM = 3
SUPPORT = 4
HALO_LENGTH = 2
DEPTH_WEIGTH = [1, 1]
ISURPRISINGNESS_REPORT_THRESHOLD = 0
EPOCHS = 10000
NORMALIZED_ISURPRISINGNESS = False

In [3]:
assert len(DEPTH_WEIGTH) == HALO_LENGTH
halo_levels = [i for i in range(HALO_LENGTH)]
if TARGET_NODES is None:
    atomspace_nodes = db.get_matched_node_name(TARGET_TYPE, TARGET_SUBSTRING)
    print(atomspace_nodes)
    TARGET_NODES = [Node(TARGET_TYPE, db.get_node_name(h)) for h in atomspace_nodes]
print(f"TARGET_NODES = {TARGET_NODES}")

TARGET_NODES = [<Concept: ugly>]


In [6]:
def print_ordered_assignment(assignment):
    if assignment is not None:
        for key, value in assignment.mapping.items():
            print(f"{key}: {db.get_node_name(value)}")

def print_unordered_assignment(assignment):
    if assignment is not None:
        symbols = []
        for key in assignment.symbols:
            for i in range(assignment.symbols[key]):
                symbols.append(key)
        values = []
        for key in assignment.values:
            for i in range(assignment.values[key]):
                values.append(key)
        mapping_keys = []
        mapping_values = []
        for symbol, value in zip(symbols, values):
            mapping_keys.append(symbol)
            mapping_values.append(db.get_node_name(value))
        print(f"{mapping_keys} = {mapping_values}")
        
def build_pattern_from_template(template):
    targets = []
    count_variables = 1
    for target in template[1:]:
        if target == WILDCARD:
            targets.append(Variable(f"V{count_variables}"))
            count_variables += 1
        else:
             node_document = das.get_atom(target, output_format=QueryOutputFormat.ATOM_INFO)
             targets.append(Node(node_document['type'], node_document['name']))  
    return Link(template[0], ordered=(template[0] not in UNORDERED_LINK_TYPES), targets=targets)

def _random_selection(v):
    return v[np.random.randint(len(v))]

def random_selection(v, n=1):
    if n == 1:
        return _random_selection(v)
    assert n <= (len(v) / 2)
    a = v.copy()
    selected = []
    for i in range(n):
        s = _random_selection(a)
        a.remove(s)
        selected.append(s)
    return selected

def build_roulette(w):
    answer = []
    s = sum(w)
    acc = 0
    for v in w:
        acc += v / s
        answer.append(acc)
    answer[-1] = 1
    return answer

def roulette_selection(v, w):
    assert len(v) == len(w)
    random = np.random.random()
    for i in range(len(v)):
        if random <= w[i]:
            return v[i]
    
def compute_count(logical_expression):
    query_answer = PatternMatchingAnswer()
    matched = logical_expression.matched(db, query_answer)
    return len(query_answer.assignments) if matched else 0
        
def prob(count):
    return count / universe_size

def compute_isurprisingness(count, terms, term_handles, counts, normalized = False):
    n = len(term_handles)
    if n == 2:
        subset_probs = [prob(counts[0]) * prob(counts[1])]
    elif n == 3:
        subset_probs = [
            prob(counts[0]) * prob(counts[1]) * prob(counts[2]),
            prob(compute_count(And([terms[0], terms[1]]))) * prob(counts[2]), 
            prob(compute_count(And([terms[0], terms[2]]))) * prob(counts[1]),
            prob(compute_count(And([terms[1], terms[2]]))) * prob(counts[0])
        ]
    elif n == 4:
        subset_probs = [
            prob(counts[0]) * prob(counts[1]) * prob(counts[2]) * prob(counts[3]),
            prob(compute_count(And([terms[0], terms[1]]))) * prob(compute_count(And([terms[2], terms[3]]))),
            prob(compute_count(And([terms[0], terms[2]]))) * prob(compute_count(And([terms[1], terms[3]]))),
            prob(compute_count(And([terms[0], terms[3]]))) * prob(compute_count(And([terms[1], terms[2]]))),
            prob(compute_count(And([terms[0], terms[1], terms[2]]))) * prob(counts[3]),
            prob(compute_count(And([terms[0], terms[1], terms[3]]))) * prob(counts[2]),
            prob(compute_count(And([terms[0], terms[2], terms[3]]))) * prob(counts[1]),
            prob(compute_count(And([terms[1], terms[2], terms[3]]))) * prob(counts[0])
        ]
    else:
        raise NotImplementedError()
    p = prob(count)
    isurprisingness = max([p - max(subset_probs), min(subset_probs) - p])
    if normalized:
        return isurprisingness / p
    else:
        return isurprisingness
    
def build_patterns(links):
    pattern = {}
    pattern_count = {}
    for link in links:
        link_document = das.get_atom(link, output_format=QueryOutputFormat.ATOM_INFO)
        targets = link_document['targets']
        link_type = link_document['type']
        arity = len(targets)
        if arity == 2:
            templates = [
                [link_type, WILDCARD, targets[1]],
                [link_type, targets[0], WILDCARD],
                #[link_type, WILDCARD, WILDCARD],
            ]
        elif arity == 3:
            templates = [
                [link_type, WILDCARD, targets[1], targets[2]],
                [link_type, targets[0], WILDCARD, targets[2]],
                [link_type, targets[0], targets[1], WILDCARD],
                [link_type, WILDCARD, WILDCARD, targets[2]],
                [link_type, WILDCARD, targets[1], WILDCARD],
                [link_type, targets[0], WILDCARD, WILDCARD],
                #[link_type, WILDCARD, WILDCARD, WILDCARD],
            ]
        else:
            raise NotImplementedError()
        for template in templates:
            template_handle = ExpressionHasher.composite_hash(template)
            pattern[template_handle] = build_pattern_from_template(template)
            pattern_count[template_handle] = len(das.get_links(template[0], None, template[1:]))
    return tuple([pattern, pattern_count])
        
def build_composite_pattern(terms):
    assert len(terms) > 1
    for i in range(len(terms)):
        if i == 0:
            first_term = terms[i]
        else:
            second_term = terms[i]
            composite_pattern = And([first_term, second_term])
            first_term = composite_pattern
    return composite_pattern
    
def print_query(pattern):
    print(pattern)
    query_answer = PatternMatchingAnswer()
    pattern.matched(db, query_answer)
    for assignment in query_answer.assignments:
        if type(assignment) is OrderedAssignment:
            print_ordered_assignment(assignment)
        elif type(assignment) is UnorderedAssignment:
            print_unordered_assignment(assignment)
        elif type(assignment) is CompositeAssignment:
            print_ordered_assignment(assignment.ordered_mapping)
            for unordered_assignment in assignment.unordered_mappings:
                print_unordered_assignment(unordered_assignment)
        print("")
        
halo_level_roulette = build_roulette(DEPTH_WEIGTH)

In [7]:
node_handle_list = set([ExpressionHasher.terminal_hash(n.atom_type, n.name) for n in TARGET_NODES])
links = [set() for i in range(HALO_LENGTH)]
for level in range(HALO_LENGTH):
    new_level_node_handles = set()
    for node_handle in node_handle_list:
        for template in [[node_handle, WILDCARD], [WILDCARD, node_handle]]:
            link_list = set(das.get_links(None, None, template))
            for link in link_list:
                link_document = das.get_atom(link, output_format=QueryOutputFormat.ATOM_INFO)
                for h in link_document["targets"]:
                    new_level_node_handles.add(h)
            links[level].update(link_list)
    node_handle_list.update(new_level_node_handles)
for level in range(HALO_LENGTH):
    if level == 0:
        all_links = set([link for link in links[level]])
    else:
        links[level] = links[level].difference(all_links)
        all_links.update(links[level])
universe_size = len(all_links)

In [8]:
total = 0
for level in range(HALO_LENGTH):
    total += len(links[level])
    print(len(links[level]))
print("----------")
print(total)
#links

10
25
----------
35


In [9]:
pattern = [None for i in range(HALO_LENGTH)]
pattern_count = [None for i in range(HALO_LENGTH)]
pattern_handles = [None for i in range(HALO_LENGTH)]
all_patterns = {}
all_patterns_count = {}
for level in range(HALO_LENGTH):
    pattern[level], pattern_count[level] = build_patterns(links[level])
    pattern_handles[level] = [key for key in pattern[level].keys()]
    for key, value in pattern[level].items():
        all_patterns[key] = value
    for key, value in pattern_count[level].items():
        all_patterns_count[key] = value

In [10]:
total = 0
for level in range(HALO_LENGTH):
    total += len(pattern_handles[level])
    print(len(pattern_handles[level]))
print("----------")
print(total)
#pattern_handles

11
14
----------
25


In [11]:
higher_isurprisingness = 0
best_pattern = None
for i in range(EPOCHS):
    selected_handle = random_selection(pattern_handles[0])
    term_handles = [tuple([selected_handle, 0])]
    terms = [pattern[0][selected_handle]]
    counts = [pattern_count[0][selected_handle]]
    for i in range(NGRAM - 1):
        while True:
            selected_level = roulette_selection(halo_levels, halo_level_roulette)
            selected_handle = random_selection(pattern_handles[selected_level])
            if tuple([selected_handle, selected_level]) not in term_handles:
                break
        term_handles.append(tuple([selected_handle, selected_level]))
        terms.append(pattern[selected_level][selected_handle])
        counts.append(pattern_count[selected_level][selected_handle])
    composite_pattern = build_composite_pattern(terms)
    count = compute_count(composite_pattern)
    if count >= SUPPORT:
        isurprisingness = compute_isurprisingness(count, terms, term_handles, counts, normalized=NORMALIZED_ISURPRISINGNESS) 
        if isurprisingness > higher_isurprisingness:
            print(f"{count} {isurprisingness}: {terms} {term_handles} {counts}")
            higher_isurprisingness = isurprisingness
            best_pattern = composite_pattern
print_query(best_pattern)

node_type = Concept node_name = ugly
node_handle = fe5e4a94adf67ff4e2b4b34051a36a55
document = {'_id': 'fe5e4a94adf67ff4e2b4b34051a36a55', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'ugly', 'named_type': 'Concept'}
node_type = Concept node_name = man
node_handle = a15beea2e8b8fa0e73bc5f585c355a63
document = {'_id': 'a15beea2e8b8fa0e73bc5f585c355a63', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'man', 'named_type': 'Concept'}
node_type = Concept node_name = Abe
node_handle = ea59318dcf2f2016c170aa22503aacd3
document = {'_id': 'ea59318dcf2f2016c170aa22503aacd3', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Abe', 'named_type': 'Concept'}
node_type = Concept node_name = Abe
node_handle = ea59318dcf2f2016c170aa22503aacd3
document = {'_id': 'ea59318dcf2f2016c170aa22503aacd3', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Abe', 'named_type': 'Concept'}
node_type = Concept node_name = Emily
node_handle 

document = {'_id': '14a8ecdf07eaca0009248ace23548c69', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Davion', 'named_type': 'Concept'}
node_type = Concept node_name = human
node_handle = af12f10f9ae2002a1607ba0b47ba8407
document = {'_id': 'af12f10f9ae2002a1607ba0b47ba8407', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'human', 'named_type': 'Concept'}
node_type = Concept node_name = ugly
node_handle = fe5e4a94adf67ff4e2b4b34051a36a55
document = {'_id': 'fe5e4a94adf67ff4e2b4b34051a36a55', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'ugly', 'named_type': 'Concept'}
node_type = Concept node_name = Emily
node_handle = fd11ac68f35292d4f63dc1c71115d1f3
document = {'_id': 'fd11ac68f35292d4f63dc1c71115d1f3', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Emily', 'named_type': 'Concept'}
node_type = Concept node_name = Emily
node_handle = fd11ac68f35292d4f63dc1c71115d1f3
document = {'_id': 'fd11ac68f35292d4f

document = {'_id': 'df6088a01caf3ac039db93cfda205a35', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Lily', 'named_type': 'Concept'}
node_type = Concept node_name = Allen
node_handle = b610b2d178777d54f2840155dfe1a9ec
document = {'_id': 'b610b2d178777d54f2840155dfe1a9ec', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Allen', 'named_type': 'Concept'}
node_type = Concept node_name = Abe
node_handle = ea59318dcf2f2016c170aa22503aacd3
document = {'_id': 'ea59318dcf2f2016c170aa22503aacd3', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Abe', 'named_type': 'Concept'}
node_type = Concept node_name = Cason
node_handle = f95262f0b84b712b62b7c2c317aa682e
document = {'_id': 'f95262f0b84b712b62b7c2c317aa682e', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Cason', 'named_type': 'Concept'}
node_type = Concept node_name = woman
node_handle = 2d1db3aedc5e87ab9cfe4e755d45a377
document = {'_id': '2d1db3aedc5e87ab9cfe4

document = {'_id': '2d1db3aedc5e87ab9cfe4e755d45a377', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'woman', 'named_type': 'Concept'}
node_type = Concept node_name = Allen
node_handle = b610b2d178777d54f2840155dfe1a9ec
document = {'_id': 'b610b2d178777d54f2840155dfe1a9ec', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Allen', 'named_type': 'Concept'}
node_type = Concept node_name = man
node_handle = a15beea2e8b8fa0e73bc5f585c355a63
document = {'_id': 'a15beea2e8b8fa0e73bc5f585c355a63', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'man', 'named_type': 'Concept'}
node_type = Concept node_name = Emily
node_handle = fd11ac68f35292d4f63dc1c71115d1f3
document = {'_id': 'fd11ac68f35292d4f63dc1c71115d1f3', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Emily', 'named_type': 'Concept'}
node_type = Concept node_name = Hessley
node_handle = 2d49f6fe856d612539be9e623b6dd303
document = {'_id': '2d49f6fe856d612539

document = {'_id': '2a5554154c01f8133aa4104f69f614ce', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Sophia', 'named_type': 'Concept'}
node_type = Concept node_name = Lucy
node_handle = 7a9bd2879ee3238263d78dd9c2777320
document = {'_id': '7a9bd2879ee3238263d78dd9c2777320', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Lucy', 'named_type': 'Concept'}
node_type = Concept node_name = soda drinker
node_handle = 7daf6b600ffb0e679f0be57a8432b327
document = {'_id': '7daf6b600ffb0e679f0be57a8432b327', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'soda drinker', 'named_type': 'Concept'}
node_type = Concept node_name = Emily
node_handle = fd11ac68f35292d4f63dc1c71115d1f3
document = {'_id': 'fd11ac68f35292d4f63dc1c71115d1f3', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Emily', 'named_type': 'Concept'}
node_type = Concept node_name = Allen
node_handle = b610b2d178777d54f2840155dfe1a9ec
document = {'_id': 'b61

...

document = {'_id': 'af12f10f9ae2002a1607ba0b47ba8407', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'human', 'named_type': 'Concept'}
node_type = Concept node_name = Davion
node_handle = 14a8ecdf07eaca0009248ace23548c69
document = {'_id': '14a8ecdf07eaca0009248ace23548c69', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Davion', 'named_type': 'Concept'}
node_type = Concept node_name = Lily
node_handle = df6088a01caf3ac039db93cfda205a35
document = {'_id': 'df6088a01caf3ac039db93cfda205a35', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Lily', 'named_type': 'Concept'}
node_type = Concept node_name = Emily
node_handle = fd11ac68f35292d4f63dc1c71115d1f3
document = {'_id': 'fd11ac68f35292d4f63dc1c71115d1f3', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Emily', 'named_type': 'Concept'}
node_type = Concept node_name = Davion
node_handle = 14a8ecdf07eaca0009248ace23548c69
document = {'_id': '14a8ecdf07eaca0

document = {'_id': 'b610b2d178777d54f2840155dfe1a9ec', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Allen', 'named_type': 'Concept'}
node_type = Concept node_name = Alaura
node_handle = a04f9d57b909a40d5e6b8c49e94b03cd
document = {'_id': 'a04f9d57b909a40d5e6b8c49e94b03cd', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Alaura', 'named_type': 'Concept'}
node_type = Concept node_name = Lucy
node_handle = 7a9bd2879ee3238263d78dd9c2777320
document = {'_id': '7a9bd2879ee3238263d78dd9c2777320', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Lucy', 'named_type': 'Concept'}
node_type = Concept node_name = Cason
node_handle = f95262f0b84b712b62b7c2c317aa682e
document = {'_id': 'f95262f0b84b712b62b7c2c317aa682e', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Cason', 'named_type': 'Concept'}
node_type = Concept node_name = Emily
node_handle = fd11ac68f35292d4f63dc1c71115d1f3
document = {'_id': 'fd11ac68f35292d4

document = {'_id': 'f95262f0b84b712b62b7c2c317aa682e', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Cason', 'named_type': 'Concept'}
node_type = Concept node_name = Allen
node_handle = b610b2d178777d54f2840155dfe1a9ec
document = {'_id': 'b610b2d178777d54f2840155dfe1a9ec', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Allen', 'named_type': 'Concept'}
node_type = Concept node_name = Cason
node_handle = f95262f0b84b712b62b7c2c317aa682e
document = {'_id': 'f95262f0b84b712b62b7c2c317aa682e', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Cason', 'named_type': 'Concept'}
node_type = Concept node_name = ugly
node_handle = fe5e4a94adf67ff4e2b4b34051a36a55
document = {'_id': 'fe5e4a94adf67ff4e2b4b34051a36a55', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'ugly', 'named_type': 'Concept'}
node_type = Concept node_name = Lily
node_handle = df6088a01caf3ac039db93cfda205a35
document = {'_id': 'df6088a01caf3ac039d

document = {'_id': 'fd11ac68f35292d4f63dc1c71115d1f3', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Emily', 'named_type': 'Concept'}
node_type = Concept node_name = Lily
node_handle = df6088a01caf3ac039db93cfda205a35
document = {'_id': 'df6088a01caf3ac039db93cfda205a35', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Lily', 'named_type': 'Concept'}
node_type = Concept node_name = Abe
node_handle = ea59318dcf2f2016c170aa22503aacd3
document = {'_id': 'ea59318dcf2f2016c170aa22503aacd3', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Abe', 'named_type': 'Concept'}
node_type = Concept node_name = Allen
node_handle = b610b2d178777d54f2840155dfe1a9ec
document = {'_id': 'b610b2d178777d54f2840155dfe1a9ec', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Allen', 'named_type': 'Concept'}
node_type = Concept node_name = Lily
node_handle = df6088a01caf3ac039db93cfda205a35
document = {'_id': 'df6088a01caf3ac039db93c

document = {'_id': '14a8ecdf07eaca0009248ace23548c69', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Davion', 'named_type': 'Concept'}
node_type = Concept node_name = Allen
node_handle = b610b2d178777d54f2840155dfe1a9ec
document = {'_id': 'b610b2d178777d54f2840155dfe1a9ec', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Allen', 'named_type': 'Concept'}
node_type = Concept node_name = Hessley
node_handle = 2d49f6fe856d612539be9e623b6dd303
document = {'_id': '2d49f6fe856d612539be9e623b6dd303', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Hessley', 'named_type': 'Concept'}
node_type = Concept node_name = Davion
node_handle = 14a8ecdf07eaca0009248ace23548c69
document = {'_id': '14a8ecdf07eaca0009248ace23548c69', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Davion', 'named_type': 'Concept'}
node_type = Concept node_name = Allen
node_handle = b610b2d178777d54f2840155dfe1a9ec
document = {'_id': 'b610b2d17

In [12]:
higher_isurprisingness = 0
best_pattern = None
all_patterns_handles = all_patterns.keys()

for basic_handle in pattern_handles[0]:
    for combination_handles in combinations(all_patterns, NGRAM - 1):
        if basic_handle in combination_handles:
            continue
        term_handles = [basic_handle, *combination_handles]
        terms = [all_patterns[handle] for handle in term_handles]
        counts = [all_patterns_count[handle] for handle in term_handles]
        composite_pattern = build_composite_pattern(terms)
        count = compute_count(composite_pattern)
        if count >= SUPPORT:
            isurprisingness = compute_isurprisingness(count, terms, term_handles, counts, normalized=NORMALIZED_ISURPRISINGNESS) 
            if isurprisingness > higher_isurprisingness:
                print(f"{count} {isurprisingness}: {terms} {counts}")
                higher_isurprisingness = isurprisingness
                best_pattern = composite_pattern    
print_query(best_pattern)

node_type = Concept node_name = ugly
node_handle = fe5e4a94adf67ff4e2b4b34051a36a55
document = {'_id': 'fe5e4a94adf67ff4e2b4b34051a36a55', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'ugly', 'named_type': 'Concept'}
node_type = Concept node_name = Sophia
node_handle = 2a5554154c01f8133aa4104f69f614ce
document = {'_id': '2a5554154c01f8133aa4104f69f614ce', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Sophia', 'named_type': 'Concept'}
node_type = Concept node_name = ugly
node_handle = fe5e4a94adf67ff4e2b4b34051a36a55
document = {'_id': 'fe5e4a94adf67ff4e2b4b34051a36a55', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'ugly', 'named_type': 'Concept'}
node_type = Concept node_name = Sophia
node_handle = 2a5554154c01f8133aa4104f69f614ce
document = {'_id': '2a5554154c01f8133aa4104f69f614ce', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Sophia', 'named_type': 'Concept'}
node_type = Concept node_name = ugly

document = {'_id': '2d49f6fe856d612539be9e623b6dd303', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Hessley', 'named_type': 'Concept'}
node_type = Concept node_name = Lucy
node_handle = 7a9bd2879ee3238263d78dd9c2777320
document = {'_id': '7a9bd2879ee3238263d78dd9c2777320', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Lucy', 'named_type': 'Concept'}
node_type = Concept node_name = Cason
node_handle = f95262f0b84b712b62b7c2c317aa682e
document = {'_id': 'f95262f0b84b712b62b7c2c317aa682e', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Cason', 'named_type': 'Concept'}
node_type = Concept node_name = Hessley
node_handle = 2d49f6fe856d612539be9e623b6dd303
document = {'_id': '2d49f6fe856d612539be9e623b6dd303', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Hessley', 'named_type': 'Concept'}
node_type = Concept node_name = Lucy
node_handle = 7a9bd2879ee3238263d78dd9c2777320
document = {'_id': '7a9bd2879ee32

node_type = Concept node_name = woman
node_handle = 2d1db3aedc5e87ab9cfe4e755d45a377
document = {'_id': '2d1db3aedc5e87ab9cfe4e755d45a377', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'woman', 'named_type': 'Concept'}
node_type = Concept node_name = Hessley
node_handle = 2d49f6fe856d612539be9e623b6dd303
document = {'_id': '2d49f6fe856d612539be9e623b6dd303', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Hessley', 'named_type': 'Concept'}
node_type = Concept node_name = Alaura
node_handle = a04f9d57b909a40d5e6b8c49e94b03cd
document = {'_id': 'a04f9d57b909a40d5e6b8c49e94b03cd', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Alaura', 'named_type': 'Concept'}
node_type = Concept node_name = soda drinker
node_handle = 7daf6b600ffb0e679f0be57a8432b327
document = {'_id': '7daf6b600ffb0e679f0be57a8432b327', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'soda drinker', 'named_type': 'Concept'}
node_type = Conc

document = {'_id': '14a8ecdf07eaca0009248ace23548c69', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Davion', 'named_type': 'Concept'}
node_type = Concept node_name = Emily
node_handle = fd11ac68f35292d4f63dc1c71115d1f3
document = {'_id': 'fd11ac68f35292d4f63dc1c71115d1f3', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Emily', 'named_type': 'Concept'}
node_type = Concept node_name = woman
node_handle = 2d1db3aedc5e87ab9cfe4e755d45a377
document = {'_id': '2d1db3aedc5e87ab9cfe4e755d45a377', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'woman', 'named_type': 'Concept'}
node_type = Concept node_name = Davion
node_handle = 14a8ecdf07eaca0009248ace23548c69
document = {'_id': '14a8ecdf07eaca0009248ace23548c69', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Davion', 'named_type': 'Concept'}
node_type = Concept node_name = Emily
node_handle = fd11ac68f35292d4f63dc1c71115d1f3
document = {'_id': 'fd11ac68f3529

node_type = Concept node_name = Abe
node_handle = ea59318dcf2f2016c170aa22503aacd3
document = {'_id': 'ea59318dcf2f2016c170aa22503aacd3', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Abe', 'named_type': 'Concept'}
node_type = Concept node_name = Lucy
node_handle = 7a9bd2879ee3238263d78dd9c2777320
document = {'_id': '7a9bd2879ee3238263d78dd9c2777320', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Lucy', 'named_type': 'Concept'}
node_type = Concept node_name = man
node_handle = a15beea2e8b8fa0e73bc5f585c355a63
document = {'_id': 'a15beea2e8b8fa0e73bc5f585c355a63', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'man', 'named_type': 'Concept'}
node_type = Concept node_name = Abe
node_handle = ea59318dcf2f2016c170aa22503aacd3
document = {'_id': 'ea59318dcf2f2016c170aa22503aacd3', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Abe', 'named_type': 'Concept'}
node_type = Concept node_name = Lucy
node_handle =

document = {'_id': 'df6088a01caf3ac039db93cfda205a35', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Lily', 'named_type': 'Concept'}
node_type = Concept node_name = ugly
node_handle = fe5e4a94adf67ff4e2b4b34051a36a55
document = {'_id': 'fe5e4a94adf67ff4e2b4b34051a36a55', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'ugly', 'named_type': 'Concept'}
node_type = Concept node_name = Lily
node_handle = df6088a01caf3ac039db93cfda205a35
document = {'_id': 'df6088a01caf3ac039db93cfda205a35', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Lily', 'named_type': 'Concept'}
node_type = Concept node_name = ugly
node_handle = fe5e4a94adf67ff4e2b4b34051a36a55
document = {'_id': 'fe5e4a94adf67ff4e2b4b34051a36a55', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'ugly', 'named_type': 'Concept'}
node_type = Concept node_name = Lily
node_handle = df6088a01caf3ac039db93cfda205a35
document = {'_id': 'df6088a01caf3ac039db93cf

document = {'_id': 'ea59318dcf2f2016c170aa22503aacd3', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Abe', 'named_type': 'Concept'}
node_type = Concept node_name = human
node_handle = af12f10f9ae2002a1607ba0b47ba8407
document = {'_id': 'af12f10f9ae2002a1607ba0b47ba8407', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'human', 'named_type': 'Concept'}
node_type = Concept node_name = Lily
node_handle = df6088a01caf3ac039db93cfda205a35
document = {'_id': 'df6088a01caf3ac039db93cfda205a35', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Lily', 'named_type': 'Concept'}
node_type = Concept node_name = Allen
node_handle = b610b2d178777d54f2840155dfe1a9ec
document = {'_id': 'b610b2d178777d54f2840155dfe1a9ec', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Allen', 'named_type': 'Concept'}
node_type = Concept node_name = Cason
node_handle = f95262f0b84b712b62b7c2c317aa682e
document = {'_id': 'f95262f0b84b712b62b7

document = {'_id': '7a9bd2879ee3238263d78dd9c2777320', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Lucy', 'named_type': 'Concept'}
node_type = Concept node_name = soda drinker
node_handle = 7daf6b600ffb0e679f0be57a8432b327
document = {'_id': '7daf6b600ffb0e679f0be57a8432b327', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'soda drinker', 'named_type': 'Concept'}
node_type = Concept node_name = Alaura
node_handle = a04f9d57b909a40d5e6b8c49e94b03cd
document = {'_id': 'a04f9d57b909a40d5e6b8c49e94b03cd', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Alaura', 'named_type': 'Concept'}
node_type = Concept node_name = Lucy
node_handle = 7a9bd2879ee3238263d78dd9c2777320
document = {'_id': '7a9bd2879ee3238263d78dd9c2777320', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Lucy', 'named_type': 'Concept'}
node_type = Concept node_name = man
node_handle = a15beea2e8b8fa0e73bc5f585c355a63
document = {'_id': 'a15be

document = {'_id': 'a15beea2e8b8fa0e73bc5f585c355a63', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'man', 'named_type': 'Concept'}
node_type = Concept node_name = Emily
node_handle = fd11ac68f35292d4f63dc1c71115d1f3
document = {'_id': 'fd11ac68f35292d4f63dc1c71115d1f3', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Emily', 'named_type': 'Concept'}
node_type = Concept node_name = Sophia
node_handle = 2a5554154c01f8133aa4104f69f614ce
document = {'_id': '2a5554154c01f8133aa4104f69f614ce', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'Sophia', 'named_type': 'Concept'}
node_type = Concept node_name = human
node_handle = af12f10f9ae2002a1607ba0b47ba8407
document = {'_id': 'af12f10f9ae2002a1607ba0b47ba8407', 'composite_type_hash': 'd99a604c79ce3c2e76a2f43488d5d4c3', 'name': 'human', 'named_type': 'Concept'}
node_type = Concept node_name = Emily
node_handle = fd11ac68f35292d4f63dc1c71115d1f3
document = {'_id': 'fd11ac68f35292d4